# BART FINE TUNINIG AND JOB DESCRIPTION GENERATION without stopwords in resumes

In [2]:
import pandas as pd
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM
import re
import nltk
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
import re
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize
from sklearn.model_selection import train_test_split


In [3]:
import os
os.environ['CUDA_VISIBLE_DEVICES'] = '1' 

# Importing BART LARGE

In [18]:
import tensorflow as tf
from transformers import BartTokenizer, TFBartForConditionalGeneration
from transformers import TextDataset, DataCollatorForLanguageModeling, TrainingArguments, Trainer

# Load BART model and tokenizer
model = TFBartForConditionalGeneration.from_pretrained("facebook/bart-large")
tokenizer = BartTokenizer.from_pretrained("facebook/bart-large")


All model checkpoint layers were used when initializing TFBartForConditionalGeneration.

All the layers of TFBartForConditionalGeneration were initialized from the model checkpoint at facebook/bart-large.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFBartForConditionalGeneration for predictions without further training.


In [5]:
df = pd.read_csv('all_jd.csv')

In [6]:
df

Job_Designation  \
0                                       project manager   
1                      web developer,software developer   
2                     java developer,software developer   
3                                      security analyst   
4                                 network administrator   
...                                                 ...   
2424                                   security analyst   
2425                  java developer,software developer   
2426              systems administrator,project manager   
2427  software developer,python developer,web developer   
2428             network administrator,security analyst   

                                            resume_text  \
0     data center data center reston, va  systems en...   
1     senior ui developer senior ui developer senior...   
2     angularjs/ui/ java developer/lead angularjs/ui...   
3     sr. hadoop/big data developer sr. hadoop/big d...   
4     sr. python developer sr. python developer sr. ...   
...                                                 ...   
2424  sr. network administrator sr. network administ...   
2425  senior software developer senior software deve...   
2426  ui developer ui developer ui developer - cvs p...   
2427  python developer python developer python devel...   
2428  java developer java developer java developer -...   

                                                     JD  tokens  
0     Job Title: Project Manager\n\nLocation: Reston...    1874  
1     Job Title: Web Developer/Software Developer\n\...    1874  
2     Job Description: Java Developer/Software Devel...    1875  
3     Job Title: Security Analyst (Big Data/Hadoop)\...    1875  
4     Job Title: Network Administrator\n\nJob Descri...    1875  
...                                                 ...     ...  
2424  Job Title: Senior Network Administrator\n\nJob...    1579  
2425  Job Title: Senior Software Developer\n\nJob Su...    1579  
2426  UI Developer Job Description:\n\nWe are seekin...    1580  
2427  Job Title: Python Developer\n\nLocation: Cleve...    1580  
2428  Job Title: Java Developer\n\nJob Summary:\n\nW...    1580  

[2429 rows x 4 columns]

In [14]:
df.isnull().sum()

Job_Designation    0
resume_text        0
JD                 0
tokens             0
dtype: int64

# Preprocessing 

In [7]:
import re
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize

# nltk.download('stopwords')
# nltk.download('punkt')
# nltk.download('wordnet')
stop_words = set(stopwords.words('english'))
lemmatizer = WordNetLemmatizer()

def clean_text(text):
    # Replace new line characters and bullet points with a space
    text = re.sub(r'[\n•]', ' ', text)

    # Lowercase the text
    text = text.lower()

    # Remove special characters and punctuation, but keep numbers
    text = re.sub(r'[^\w\s]', '', text)

    # Tokenize the text
    tokens = word_tokenize(text)

    # Remove stop words
    filtered_tokens = [word for word in tokens if word not in stop_words]

    # Lemmatize the words
    lemmatized_tokens = [lemmatizer.lemmatize(word) for word in filtered_tokens]

    # Join the tokens back into a single string
    cleaned_text = ' '.join(lemmatized_tokens)

    return cleaned_text


In [8]:
job_descriptions = df['JD'].tolist()
resumes = df['resume_text'].tolist()

In [9]:
job_descriptions

["Job Title: Project Manager\n\nLocation: Reston, VA\n\nJob Description:\n\nWe are seeking an experienced Project Manager to join our team. The ideal candidate will have a strong background in systems engineering, ERP projects, client management, enterprise implementations, and software development processes. The candidate should be authorized to work in the US for any employer.\n\nResponsibilities:\n\n- Develop project plans, schedules, and detailed project plans using tools such as MS Project, Project Server, and other artifact templates.\n- Communicate project plans, status, and critical issues to project stakeholders and sponsors.\n- Identify all dependent tasks and resources, forecast resources, and motivate leadership skills with the ability to foster cooperation and maximum productivity in both matrix and non-matrix environments.\n- Manage project scope, schedule, and financials, evaluating the impact of key decisions on these triple constraints and escalating as required.\n- Fa

In [10]:
import tensorflow as tf
from transformers import AutoTokenizer, TFAutoModelForSeq2SeqLM, AdamW
from tensorflow.keras.callbacks import EarlyStopping

# # Load the BART-base tokenizer
# tokenizer = AutoTokenizer.from_pretrained('facebook/bart-base')

# # Preprocess and encode the job description and resume columns
# job_descriptions = []
# resumes = []

# Clean the data
job_descriptions = [clean_text(jd) for jd in job_descriptions]
resumes = [clean_text(resume) for resume in resumes]



In [40]:
job_descriptions


['job title project manager location reston va job description seeking experienced project manager join team ideal candidate strong background system engineering erp project client management enterprise implementation software development process candidate authorized work u employer responsibility develop project plan schedule detailed project plan using tool m project project server artifact template communicate project plan status critical issue project stakeholder sponsor identify dependent task resource forecast resource motivate leadership skill ability foster cooperation maximum productivity matrix nonmatrix environment manage project scope schedule financials evaluating impact key decision triple constraint escalating required facilitate project change request process maintain project document manage risk mitigation plan ensure rollout plan documented communicated facilitate implementation planning coordinate cutover activity lead postproject analysis capture lesson learned guid

In [11]:

# Combine job descriptions and resumes into a single dataset
texts = job_descriptions + resumes



In [12]:
# Tokenize the dataset
inputs = tokenizer(texts, return_tensors="tf", padding=True, truncation=True, max_length=512)



2023-04-21 19:06:26.323598: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:939] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2023-04-21 19:06:26.323920: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcufft.so.10'; dlerror: libcufft.so.10: cannot open shared object file: No such file or directory
2023-04-21 19:06:26.339967: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcusparse.so.11'; dlerror: libcusparse.so.11: cannot open shared object file: No such file or directory
2023-04-21 19:06:26.340005: W tensorflow/core/common_runtime/gpu/gpu_device.cc:1850] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the requir

In [13]:
# Create a labels tensor (same as input_ids since it's a language modeling task)
labels = tf.identity(inputs.input_ids)

# Set labels for padded tokens to -100 (ignored by the loss function)
labels = tf.where(labels == tokenizer.pad_token_id, -100, labels)


In [14]:
import numpy as np

# Convert tensors to numpy arrays
inputs_np = inputs.input_ids.numpy()
labels_np = labels.numpy()

# Split the dataset into training and validation sets
train_inputs, val_inputs, train_labels, val_labels = train_test_split(inputs_np, labels_np, test_size=0.1)

# Convert numpy arrays back to tensors
train_inputs = tf.convert_to_tensor(train_inputs)
val_inputs = tf.convert_to_tensor(val_inputs)
train_labels = tf.convert_to_tensor(train_labels)
val_labels = tf.convert_to_tensor(val_labels)


In [15]:

# Define the training and validation datasets
train_dataset = tf.data.Dataset.from_tensor_slices((train_inputs, train_labels)).batch(8)
val_dataset = tf.data.Dataset.from_tensor_slices((val_inputs, val_labels)).batch(8)


In [16]:
import tensorflow.keras.backend as K

def masked_sparse_categorical_crossentropy(y_true, y_pred):
    y_true_masked = K.maximum(y_true, 0)  # Replace -100 with 0
    mask = K.cast(K.not_equal(y_true, -100), 'float32')  # Create a mask with 1s for non-padding tokens and 0s for padding tokens
    loss = K.sparse_categorical_crossentropy(y_true_masked, y_pred, from_logits=True)  # Calculate the sparse categorical crossentropy
    loss = loss * mask  # Apply the mask to the loss
    return K.mean(loss)  # Return the mean loss


In [19]:

# Configure the model for training
optimizer = tf.keras.optimizers.Adam(learning_rate=5e-5)
loss = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True, reduction=tf.keras.losses.Reduction.NONE)
model.compile(optimizer=optimizer, loss=masked_sparse_categorical_crossentropy)



# Fine Tuning BART 

In [20]:
# Fine-tune the model
model.fit(train_dataset, epochs=1, validation_data=val_dataset)

# Save the fine-tuned model
model.save_pretrained("fine-tuned-bart")

547/547 [==============================] - 19860s 36s/step - loss: 0.1397 - val_loss: 0.0034


In [21]:
# Function to generate a job description for a new resume
def generate_job_description(model, tokenizer, resume):
    # Preprocess the resume using the clean_text function
    preprocessed_resume = clean_text(resume)

    # Tokenize the preprocessed resume
    input_ids = tokenizer.encode(preprocessed_resume, return_tensors="tf")

    # Generate a job description
    output = model.generate(input_ids, max_length=512, num_return_sequences=1, no_repeat_ngram_size=2)
    generated_text = tokenizer.decode(output[0], skip_special_tokens=True)

    return generated_text



In [23]:
df['resume_text'][1]

"senior ui developer senior ui developer senior ui developer - capital group los angeles, ca ? over 10 years of experience as a user interface/front end developer in working with various web technologies such as html/html5, css/css3, javascript framework, jquery, ajax, json, xml, sass, less and object-oriented javascript libraries like es6, angular.js, node.js, react.js, redux, backbone.js, bootstrap, responsive design. ? experience using ajax to create interactive web applications, mainly optimizing performance. ? excellent programming skills in java, c, c++, ruby, javascript, sql, pl/sql, xml technologies. ? experience in single page application reference implementation, using angularjs and browser, written in ecma script 6. ? experience on ajax techniques for data manipulation and parsing of multiple data types including xml and json. ? experience in application development processes like agile, scrum and waterfall sdlc methodologies ? designed presentation layer for dynamic web for

# Generating Job Description WITHOUT Stopwords 

In [25]:
# Generate a job description for a new resume
new_resume = "senior ui developer senior ui developer senior ui developer - capital group los angeles, ca ? over 10 years of experience as a user interface/front end developer in working with various web technologies such as html/html5, css/css3, javascript framework, jquery, ajax, json, xml, sass, less and object-oriented javascript libraries like es6, angular.js, node.js, react.js, redux, backbone.js, bootstrap, responsive design. ? experience using ajax to create interactive web applications, mainly optimizing performance. ? excellent programming skills in java, c, c++, ruby, javascript, sql, pl/sql, xml technologies. ? experience in single page application reference implementation, using angularjs and browser, written in ecma script 6. ? experience on ajax techniques for data manipulation and parsing of multiple data types including xml and json. ? experience in application development processes like agile, scrum and waterfall sdlc methodologies ? designed presentation layer for dynamic web forms using asp.net mvc 5.0 framework, html5, css3, json, angular 2 and visual studio. ? financial reports using crystal reports and xslt transformation ? experience in developing ui applications using angular js, backbone js, ext js, node js, javascript, j query, css3 ? developed application to asses json and xml from restful web service from consumer side using javascript and angular.js. ? extensive experience in angular.js 1.x/ angular 2 with creating custom directives, filters, controllers and decorators. ? experienced with vanilla javascript, including prototype, scope, and module concepts ? used d3.js for creating dynamic data visualizations and dashboards. ? good experience on quality control, jira, fish eye for tracking the tickets like accepting the tickets/defects, submitting the tickets, reviewing code and closing the tickets etc. ? experience in writing unit tests using jasmine, karma. ? experienced in various ides like web storm, notepad++, sublime text, adobe dreamweaver, microsoft visual studio code. ? strong experience in sql and database design, normalization and database management concepts. knowledgeable with rdbms concepts like writing sql queries, functions, stored procedures and pl/sql packages. ? extensive experience with version control tools including cvs, github and svn for source code version. ? used redux-saga is a redux middleware, which means this thread can be started, paused and cancelled from the main application with normal redux actions, it has access to the full redux application state and it can dispatch redux actions as well. work experience senior ui developer capital group - los angeles, ca june 2017 to present responsibilities: ? responsible for designing dynamic and multi-browser compatible pages using html 5.0, css2/css3, javascript, jquery, angular.js2, react js, json, ajax to the requirement of the client. ? used babel an ecmascript 6 to" 
generated_job_description = generate_job_description(model, tokenizer, new_resume)
print(generated_job_description)

slt transformation experience developing ui application using angular j backbone j ext j node j javascript j query css3 developed application ass json xml restful web service consumer side using javascript angularjs extensive experience Angularjs 1x angular 2 creating custom directive filter controller decorator experienced vanilla javascript including prototype scope module concept used d3js creating dynamic data visualization dashboard good experience quality control jira fish eye tracking ticket like accepting ticketsdefects submitting ticket reviewing code closing ticket etc experience writing unit test using jasmine karma experienced various ides like web storm notepad sublime text adobe dreamweaver microsoft visual studio code strong experience sql database design normalization database management concept knowledgeable rdbms concept like writing sql query function stored procedure plsql package extensive
